In [ ]:
Grassland Management Under Climate Change

In [45]:
# Import packages used for the analysis
import os
from glob import glob

import earthpy as et
import earthpy.appeears as eaapp
import geopandas as gpd
import requests
import geoviews as gv
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
import rioxarray as rxr
import xarray as xr

In [46]:
grasslands_url = (
    "https://data.fs.usda.gov/geodata/edw/edw_resources/shp"
    "/S_USA.NationalGrassland.zip")
grasslands_gdf = gpd.read_file(grasslands_url).set_index('GRASSLANDN') 
grasslands_gdf

# Select two grasslands
# Selection criteria: comparable shape, area, "similar" location
grass_gdf = (
    grasslands_gdf
    .loc[['Oglala National Grassland', 'Fort Pierre National Grassland']]
)

grass_gdf

for GRASSLANDN, grass_gs in grass_gdf.iterrows():
    print('\nGrassland name: {}'.format(GRASSLANDN))
    print(grass_gs)
    print(f"Total bounds: {grass_gs.geometry.bounds}")


Grassland name: Oglala National Grassland
NATIONALGR                                         295521010328
GIS_ACRES                                            215804.927
SHAPE_AREA                                             0.096279
SHAPE_LEN                                              1.970612
geometry      POLYGON ((-103.72476827000003 43.0009967600000...
Name: Oglala National Grassland, dtype: object
Total bounds: (-104.05313982000001, 42.74092908, -103.36517901000002, 43.00177636000001)

Grassland name: Fort Pierre National Grassland
NATIONALGR                                         281771010328
GIS_ACRES                                            209044.225
SHAPE_AREA                                             0.095149
SHAPE_LEN                                              1.455518
geometry      POLYGON ((-100.08408953000003 44.2816249699999...
Name: Fort Pierre National Grassland, dtype: object
Total bounds: (-100.47626474999998, 43.977281059999996, -100.06625771, 44.2816249

In [117]:
# Index of /POLARIS/PROPERTIES/v1.0/ph/mean/60_100
# Soil variable
# Change it according to chosen grassland units 
# (unit might not fit into one tile: 
# load in more than one tile per grassland 
# and need to merge with rioxarray (greenspace assignment)
# Download data and load it back again (ndvi assignment)

# Probably I need a function (only loop?)
# since I have two different 
# set of min values (from total bounds)

min_lat, min_lon = 42, -104
max_lat, max_lon = min_lat+1, min_lon+1
polaris_url_format = (
    "http://hydrology.cee.duke.edu/POLARIS/PROPERTIES/v1.0"
    "/ph/mean/60_100/lat{min_lat}{max_lat}_lon{min_lon}{max_lon}.tif"
)

polaris_url_oglala = polaris_url_format.format(
    min_lat=min_lat, min_lon=min_lon, max_lat=max_lat, max_lon=max_lon)

polaris_oglala_da = rxr.open_rasterio(polaris_url_oglala, masked=True).squeeze()

# polaris_oglala_da.hvplot(rasterize=True)*grass_gdf.hvplot()

min_lat, min_lon = 43, -100
max_lat, max_lon = min_lat+1, min_lon+1
polaris_url_format = (
    "http://hydrology.cee.duke.edu/POLARIS/PROPERTIES/v1.0"
    "/ph/mean/60_100/lat{min_lat}{max_lat}_lon{min_lon}{max_lon}.tif"
)

polaris_url_fp = polaris_url_format.format(
    min_lat=min_lat, min_lon=min_lon, max_lat=max_lat, max_lon=max_lon)

polaris_fp_da = rxr.open_rasterio(polaris_url_fp, masked=True).squeeze()

# polaris_fp_da.hvplot(rasterize=True)


:DynamicMap   []
   :Image   [y,x]   (value)

In [21]:
# Separated grassland gdfs

# oglala_gdf = (
#     grasslands_gdf
#     .loc[['Oglala National Grassland']]
# )
# fp_gdf = (
#     grasslands_gdf
#     .loc[['Fort Pierre National Grassland']]
# )

In [ ]:
# https://lpdaac.usgs.gov/products/srtmgl1v003/
# Elevation data

oglala_gdf = (
    grasslands_gdf
    .set_index('GRASSLANDN')
    .loc[['Oglala National Grassland']]
)

# might be the looping variable
download_key ='Oglala-SRTM'

srtm_downloader_oglala = eaapp.AppeearsDownloader(
    download_key = download_key,
    product='SRTMGL1_NC.003',
    layer='SRTMGL1_DEM',
    start_date='02-11-2000',
    end_date='02-21-2000',
    polygon=oglala_gdf)
srtm_downloader_oglala.download_files()

In [ ]:
# https://lpdaac.usgs.gov/products/srtmgl1v003/
# Elevation data

fort_pierre_gdf = (
    grasslands_gdf
    .set_index('GRASSLANDN')
    .loc[['Fort Pierre National Grassland']]
)

# might be the looping variable
download_key ='Fort-Pierre-SRTM'

srtm_downloader_fp = eaapp.AppeearsDownloader(
    download_key = download_key,
    product='SRTMGL1_NC.003',
    layer='SRTMGL1_DEM',
    start_date='02-11-2000',
    end_date='02-21-2000',
    polygon=fort_pierre_gdf)
srtm_downloader_fp.download_files()

In [104]:
# function for srtm download, final part needs work
# srtm_paths
# Should I set a data directory in the beginning of the final project to avoid this issue?

def download_srtm_data(name, geometry):
    """
    Download SRTM raster for a given geometry, start date, and end date
    
    Downloads data from NASA Shuttle Radar Topography Mission (SRTM)
    given a spatial and temporal extent. NASA Shuttle Radar 
    Topography Mission Global 1 arc second launched 
    February 11, 2000 and ﬂew for 11 days.
    <https://lpdaac.usgs.gov/products/srtmgl1v003/>

    Parameters
    ==========
    name : str
      The name used to label the download
    grasspolygon : geopandas.GeoDataFrame
      The geometry to derive the download extent from. 
      Must have a `.envelope` attribute.

    Returns
    =======
    downloader : earthpy.earthexplorer.EarthExplorerDownloader
      Object with information about the download, including the data directory.
    """
    
    print(f'\nGRASSLANDN: {name}')
    srtm_downloader = eaapp.AppeearsDownloader(
        download_key = name.lower().replace(' ', '-'),
        product='SRTMGL1_NC.003',
        layer='SRTMGL1_DEM',
        start_date='02-11-2000',
        end_date='02-21-2000',
        polygon=geometry,
        ea_dir=os.path.join(et.io.HOME, 'earth-analytics')
    )
    if not os.path.exists(srtm_downloader.data_dir):
        srtm_downloader.submit_task_request()
        srtm_downloader.download_files()
    return srtm_downloader

srtm_paths = {}
for GRASSLANDN, grass_gs in grass_gdf.iterrows():
    print('\nGrassland name: {}'.format(GRASSLANDN))
    print(grass_gs)
    print(f"Total bounds: {grass_gs.geometry.bounds}")
    srtm_downloader = (
        download_srtm_data(GRASSLANDN, grass_gdf.loc[[GRASSLANDN]])
        )
    srtm_paths[GRASSLANDN]=(glob(
        os.path.join(
            srtm_downloader.data_dir,
            'SRTMGL1_NC.003*',
            '*.tif')
    ))
srtm_paths


Grassland name: Oglala National Grassland
NATIONALGR                                         295521010328
GIS_ACRES                                            215804.927
SHAPE_AREA                                             0.096279
SHAPE_LEN                                              1.970612
geometry      POLYGON ((-103.72476827000003 43.0009967600000...
Name: Oglala National Grassland, dtype: object
Total bounds: (-104.05313982000001, 42.74092908, -103.36517901000002, 43.00177636000001)

GRASSLANDN: Oglala National Grassland

Grassland name: Fort Pierre National Grassland
NATIONALGR                                         281771010328
GIS_ACRES                                            209044.225
SHAPE_AREA                                             0.095149
SHAPE_LEN                                              1.455518
geometry      POLYGON ((-100.08408953000003 44.2816249699999...
Name: Fort Pierre National Grassland, dtype: object
Total bounds: (-100.47626474999998, 43.977

{'Oglala National Grassland': ['C:\\Users\\lucap\\earth-analytics\\oglala-national-grassland\\SRTMGL1_NC.003_2000001_to_2023348\\SRTMGL1_NC.003_SRTMGL1_DEM_doy2000042_aid0001.tif'],
 'Fort Pierre National Grassland': ['C:\\Users\\lucap\\earth-analytics\\fort-pierre-national-grassland\\SRTMGL1_NC.003_2000001_to_2023348\\SRTMGL1_NC.003_SRTMGL1_DEM_doy2000042_aid0001.tif']}

In [107]:
srtm_paths

{'Oglala National Grassland': ['C:\\Users\\lucap\\earth-analytics\\oglala-national-grassland\\SRTMGL1_NC.003_2000001_to_2023348\\SRTMGL1_NC.003_SRTMGL1_DEM_doy2000042_aid0001.tif'],
 'Fort Pierre National Grassland': ['C:\\Users\\lucap\\earth-analytics\\fort-pierre-national-grassland\\SRTMGL1_NC.003_2000001_to_2023348\\SRTMGL1_NC.003_SRTMGL1_DEM_doy2000042_aid0001.tif']}

In [111]:
# Define function for opening the downloaded
# SRTM data for chosen grasslands

def load_srtm(name, srtm_paths):
    """
    Load in and merge downloaded srtm

    Parameters
    ==========
    name : str
      The name used to label the download
    srtm_paths : dict 
        path to srtm files

    Returns
    =======
    srtm_gdf: rxr.DataArray
      DataArray with the srtm data
    """
    
    print(f'\nGRASSLANDN: {name}')
    grass_srtm_da = (
        rxr.open_rasterio(srtm_paths[name][0], masked = True)
         .squeeze()
    )
    return grass_srtm_da

# [rxr.open_rasterio(srtm_path, masked=True).squeeze() for srtm_path in srtm_paths][0]

In [114]:
oglala_srtm_da = load_srtm('Oglala National Grassland', srtm_paths)
fort_pierre_srtm_da = load_srtm('Fort Pierre National Grassland', srtm_paths)
oglala_srtm_da
fort_pierre_srtm_da


GRASSLANDN: Oglala National Grassland

GRASSLANDN: Fort Pierre National Grassland


<xarray.DataArray (y: 1097, x: 1477)>
[1620269 values with dtype=float32]
Coordinates:
    band         int32 1
  * x            (x) float64 -100.5 -100.5 -100.5 ... -100.1 -100.1 -100.1
  * y            (y) float64 44.28 44.28 44.28 44.28 ... 43.98 43.98 43.98 43.98
    spatial_ref  int32 0
Attributes:
    add_offset:     0.0
    AREA_OR_POINT:  Area
    scale_factor:   1.0
    units:          Meters

In [8]:
# Historic precipitation data 1980 12 months:

# Have a loop/function to download two climate variables?
# input variables: precip, relative humidity, rcp projection
# 
# for variable, projection...
# open('maca.nc', 'wb') as maca_file:
# 


maca_url = (
    "http://thredds.northwestknowledge.net:8080/thredds/ncss"
    "/agg_macav2metdata_pr_CCSM4_r6i1p1_historical_1950_2005_CONUS_monthly.nc"
    "?var=precipitation"
    "&?disableLLSubset=on"
    "&disableProjSubset=on"
    "&horizStride=1"
    "&time_start=1980-01-15T00%3A00%3A00Z"
    "&time_end=1980-12-15T00%3A00%3A00Z"
    "&timeStride=1&accept=netcdf"
)

maca_response = requests.get(maca_url)

# cotext manager
with open('maca.nc', 'wb') as maca_file:
    maca_file.write(maca_response.content)

In [101]:
maca_url

'http://thredds.northwestknowledge.net:8080/thredds/ncss/agg_macav2metdata_pr_CCSM4_r6i1p1_historical_1950_2005_CONUS_monthly.nc?var=precipitation&?disableLLSubset=on&disableProjSubset=on&horizStride=1&time_start=1980-01-15T00%3A00%3A00Z&time_end=1980-12-15T00%3A00%3A00Z&timeStride=1&accept=netcdf'

In [14]:
maca_ds = xr.open_dataset('maca.nc')
# Reassign coordinates
maca_ds = maca_ds.assign_coords(lon=maca_ds.lon-360)

# Pull out precipitation variable to work with dataarray
precip_da = maca_ds.precipitation

#Directly write the crs
precip_da.rio.write_crs("epsg:4326", inplace=True)

# Set the spatial dimensions
precip_da.rio.set_spatial_dims('lon', 'lat', inplace=True)

# precip_da.mean('time').hvplot(rasterize=True) * oglala_gdf.hvplot()

:DynamicMap   []
   :Overlay
      .Image.I    :Image   [lon,lat]   (precipitation)
      .Polygons.I :Polygons   [x,y]

In [15]:
oglala_gdf.total_bounds

array([-104.05313982,   42.74092908, -103.36517901,   43.00177636])

In [22]:
# funtion for clipping the grassland gdfs to the climate variables
# two locations two variables

precip_oglala_clip = precip_da.rio.clip(oglala_gdf.geometry).mean('time').hvplot()

precip_oglala_clipbox = (
    precip_da.rio.clip_box(*oglala_gdf.total_bounds)
    .mean('time')
    .hvplot()
)

precip_fp_clip = precip_da.rio.clip(fort_pierre_gdf.geometry).mean('time').hvplot()

precip_fp_clipbox = (
    precip_da.rio.clip_box(*fort_pierre_gdf.total_bounds)
    .mean('time')
    .hvplot()
)

precip_fp_clipbox

:Image   [lon,lat]   (precipitation)

Calculate at least one derived topographic variable (slope or aspect)

In [43]:
# load the srtm polygons(?) for both grasslands
# import xarray-spatial as xrspatial


ModuleNotFoundError: No module named 'xarray_spatial'

In [100]:
# EPSG:4269 NAD83 - change to 4326 (WGS84)?
grass_gdf.crs

<Geographic 2D CRS: EPSG:4269>
Name: NAD83
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: North America - onshore and offshore: Canada - Alberta; British Columbia; Manitoba; New Brunswick; Newfoundland and Labrador; Northwest Territories; Nova Scotia; Nunavut; Ontario; Prince Edward Island; Quebec; Saskatchewan; Yukon. Puerto Rico. United States (USA) - Alabama; Alaska; Arizona; Arkansas; California; Colorado; Connecticut; Delaware; Florida; Georgia; Hawaii; Idaho; Illinois; Indiana; Iowa; Kansas; Kentucky; Louisiana; Maine; Maryland; Massachusetts; Michigan; Minnesota; Mississippi; Missouri; Montana; Nebraska; Nevada; New Hampshire; New Jersey; New Mexico; New York; North Carolina; North Dakota; Ohio; Oklahoma; Oregon; Pennsylvania; Rhode Island; South Carolina; South Dakota; Tennessee; Texas; Utah; Vermont; Virginia; Washington; West Virginia; Wisconsin; Wyoming. US Virgin Islands. British Virgin Islands

Harmonize data

In [ ]:
# load in soil ph (2), 
# elevation (2) and/or(?) slope (2),
# clipped climate variable (2x2)
# ds.rio.reproject_match()